In [1]:
%reload_ext autoreload
%autoreload 2

In [2]:
# Standard library imports
from pathlib import Path
from typing import Dict, Any
import pickle
import joblib

# Third-party imports
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.io as pio
from scipy.stats import ttest_ind
import optuna
from sklearn.base import BaseEstimator, ClassifierMixin
from sklearn.metrics import (
    precision_score, recall_score, f1_score, 
    precision_recall_curve, auc, confusion_matrix,
)
from sklearn.model_selection import (
    train_test_split, RepeatedStratifiedKFold, KFold
)
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC
from imblearn.combine import SMOTEENN
from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import EditedNearestNeighbours
from sklearn.utils import resample
from churn.modelling import ThresholdedSVC
from churn.modelling import (
    eval_model_performance,
    bootstrap_cate,  
    eval_model_performance,
    split_and_subset, 
    custom_f1_scorer,
    objective_causal
)
# CausalML imports
from causalml.inference.meta import BaseSClassifier, BaseTClassifier, BaseXClassifier

# Local application imports
import churn.config as cfg
from churn.paths import create_directories, DATA_DIR
from churn.preprocessing import load_data

from churn.analytics import (
    aggregate_by_variable, 
    display_numeric_results, 
    aggregate_categorical_variables,
    display_categorical_results, 
    perform_ttest,
    calculate_cate_estimates, 
    print_cate_statistics,
    separate_treatment_variable,
    scale_features,
    add_treatment_variable,
    define_cate_variables,
    get_top_customers_for_treatment
    )
from churn.plot import plot_ecdf_plots, create_histogram

from churn.paths import DATA_DIR, MODELS_DIR
# Enable inline plotting for Jupyter notebooks
%matplotlib inline

In [3]:
# Define the cross-validation strategy
cv = RepeatedStratifiedKFold(n_splits=cfg.N_SPLITS, n_repeats=cfg.N_REPEATS, random_state=cfg.SEED)

# To check the robustnes of the treatment_effect
kf = KFold(n_splits=cfg.N_SPLITS, shuffle=True, random_state=cfg.SEED)

# Initialize the scaler
scaler = StandardScaler()

In [4]:
# Path to the raw data
create_directories()
file_path = Path(DATA_DIR / 'churn.parquet')

2024-09-07 17:26:38,319 - INFO - Folder "data" ensured at "/Users/borja/Documents/Somniumrema/projects/ml/churn/data"
2024-09-07 17:26:38,323 - INFO - Folder "models" ensured at "/Users/borja/Documents/Somniumrema/projects/ml/churn/models"


In [5]:
# Load the raw data
raw = load_data(file_path) 
# Display the first rows of the raw data
raw.head()

2024-09-07 17:26:38,410 - INFO - Data loaded from /Users/borja/Documents/Somniumrema/projects/ml/churn/data/churn.parquet


area_code  plan  n_sms  total_day_minutes  total_day_calls  \
237522        5.0   2.0    724        1365.991021              203   
847276        2.0   3.0    387        1253.394397              158   
242450        8.0   1.0    490         627.687099              165   
377221        3.0   1.0    822         601.816333              115   
991506        1.0   2.0    455         951.019715              140   

        total_day_charge  total_eve_minutes  total_eve_calls  \
237522         50.449691         681.643301              140   
847276         77.050620         437.941533               88   
242450         42.508170         618.231970               54   
377221         72.020707         605.255759              106   
991506         44.885685         320.538743               75   

        total_eve_charge  total_night_minutes  total_night_calls  \
237522         33.122690           157.639198                 53   
847276         20.629900           220.159029                 32   
242450         17.826781           178.298004                 85   
377221         27.550356           212.695526                 30   
991506         25.209541           217.364011                 98   

        total_night_charge  customer_service_calls  customer_service_rating  \
237522           25.163988                      14                        8   
847276           58.178678                       0                        8   
242450           47.785126                      32                        5   
377221            6.765252                      25                        9   
991506           25.802669                      36                        6   

        customer_hapiness  churn  
237522           0.298234      0  
847276           0.424740      0  
242450           0.378805      1  
377221           0.175085      0  
991506           0.612607      0

In [6]:
# Calculate the proportion of churn and print the results using method chaining
Churn_proportion = (
    raw.assign(churn=pd.to_numeric(raw['churn'], errors='coerce'))
       .loc[:, 'churn']
       .mean()
)

# Print the results
print(f"{Churn_proportion = :.2%}")

Churn_proportion = 8.71%


In [7]:
# Display the data types of the raw data
raw.info()

<class 'pandas.core.frame.DataFrame'>
Index: 7500 entries, 237522 to 794745
Data columns (total 16 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   area_code                7500 non-null   float64
 1   plan                     7500 non-null   float64
 2   n_sms                    7500 non-null   int64  
 3   total_day_minutes        7500 non-null   float64
 4   total_day_calls          7500 non-null   int64  
 5   total_day_charge         7500 non-null   float64
 6   total_eve_minutes        7500 non-null   float64
 7   total_eve_calls          7500 non-null   int64  
 8   total_eve_charge         7500 non-null   float64
 9   total_night_minutes      7500 non-null   float64
 10  total_night_calls        7500 non-null   int64  
 11  total_night_charge       7500 non-null   float64
 12  customer_service_calls   7500 non-null   int64  
 13  customer_service_rating  7500 non-null   int64  
 14  customer_hapiness     

In [8]:
# Rename column 'customer_hapiness' and apply the correct type to the variables
raw = (
    raw
       .rename(columns={'customer_hapiness': 'customer_happiness'})
       .assign(
    area_code=lambda df: df['area_code'].astype('category'),
    plan=lambda df: df['plan'].astype('category'),
    churn=lambda df: df['churn'].astype('category'),
    total_day_minutes=lambda df: np.round(df['total_day_minutes']),
    total_day_calls=lambda df: np.round(df['total_day_calls']),
    total_day_charge=lambda df: np.round(df['total_day_charge'], 2),
    total_eve_minutes=lambda df: np.round(df['total_eve_minutes']),
    total_eve_calls=lambda df: np.round(df['total_eve_calls']),
    total_eve_charge=lambda df: np.round(df['total_eve_charge'], 2),
    total_night_minutes=lambda df: np.round(df['total_night_minutes']),
    total_night_calls=lambda df: np.round(df['total_night_calls']),
    total_night_charge=lambda df: np.round(df['total_night_charge'], 2)
    )
)

In [9]:
# Select all numerical columns except for 'churn'
variables = raw.select_dtypes(include=[np.number]).columns

# Aggregate the data by the 'churn' variable
results = aggregate_by_variable(raw, variables)

# Dispplay relationships between numerical variables and churn
display_numeric_results(results)

In [10]:
# Aggregate the data by the categorical variables
results = aggregate_categorical_variables(raw, "churn")

# Display relationships between categorical variables and churn
display_categorical_results(results)

In [11]:
# Plot the ECDF plots for variables
plot_ecdf_plots(raw, raw, 'churn')

In [12]:
# Correlation matrix to identify which features are correlated with churn
correlation_with_churn = raw.corr()['churn'].sort_values(ascending=False) 

# Display results
correlation_with_churn

churn                      1.000000
customer_service_calls     0.523331
total_day_calls            0.028605
n_sms                      0.017339
total_day_minutes          0.009359
total_eve_minutes          0.005191
total_eve_calls            0.004448
total_day_charge           0.001568
area_code                 -0.003627
total_night_calls         -0.004328
total_night_minutes       -0.007464
plan                      -0.008527
total_eve_charge          -0.008754
total_night_charge        -0.010278
customer_service_rating   -0.143524
customer_happiness        -0.224964
Name: churn, dtype: float64

In [13]:
# Define the threshold for the treatment variable
threshold = 20

# Create binary treatment variable based on whether the bin is greater than or equal to the bin for 41
raw['treatment'] = np.where(raw['customer_service_calls'] <= threshold, 1, 0)

In [14]:
# Selecte the most important features
features = ['customer_service_calls', 'customer_service_rating', 'customer_happiness', 'treatment']

# Define the features and target variable
X = raw[features]
y = raw['churn']

In [15]:
# Split the dataset into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(
    X, 
    y, 
    test_size=cfg.TEST_SIZE, 
    random_state=cfg.SEED, 
    stratify=raw['churn']
)

In [16]:
# Column name for the treatment variable
treatment_col = 'treatment'

# Separate the treatment variable
treatment_train, treatment_test, X_train, X_test = separate_treatment_variable(X_train, X_test, treatment_col)

# Scale the features
X_train_scaled, X_test_scaled = scale_features(X_train, X_test, scaler)

# Add the treatment variable back to the scaled datasets
X_train_scaled, X_test_scaled = add_treatment_variable(X_train_scaled, X_test_scaled, treatment_train, treatment_test, treatment_col)

In [17]:
# Define the objective function for the causal model
study = optuna.create_study(direction='maximize')

# Optimize the causal model
study.optimize(lambda trial: objective_causal(trial, X_train_scaled, y_train), n_trials = cfg.SEED)

# Get the best trial
best_trial = study.best_trial

# Display the best hyperparameters and the best F1 score
print(f"Best hyperparameters: {best_trial.params}")
print(f'Best F1 Score: {best_trial.value}')

Best hyperparameters: {'C': 11.599674210852156}
Best F1 Score: 0.702685704292597


In [18]:
# Refit the model on the entire training dataset with the best hyperparameters
svc_model = SVC(C=best_trial.params['C'], kernel='linear', class_weight='balanced', probability=True)

# Handle class imbalance with SMOTEENN
smote_enn = SMOTEENN(smote=SMOTE(sampling_strategy='minority'), enn=EditedNearestNeighbours())
X_train_res, y_train_res = smote_enn.fit_resample(X_train_scaled, y_train)

# Fit the model on the resampled data
svc_model.fit(X_train_res, y_train_res)

# Store the best threshold separately
best_threshold = custom_f1_scorer(y_train, svc_model.predict_proba(X_train_scaled))['best_threshold']

# Print results
print(f'Best Threshold: {best_threshold}')

Best Threshold: 0.9


In [19]:
# Save model with best threshold
thresholded_svc = ThresholdedSVC(base_model=svc_model, threshold=best_threshold)

# Serialize the trained model
model_filename = Path(MODELS_DIR / 'thresholded_svc.pkl')
joblib.dump(thresholded_svc, model_filename)

# Inform that the model has been saved
print("Model saved as thresholded_svc.pkl")

Model saved as thresholded_svc.pkl


In [20]:
# Load the optimized SVC model
model_filename = Path(MODELS_DIR / 'thresholded_svc.pkl')
t_svc_model = joblib.load(model_filename)

# Get the parameters of the loaded SVC model
svc_params = t_svc_model.get_params()
print("SVC Model Parameters:")
print(svc_params)

SVC Model Parameters:
{'base_model__C': 11.599674210852156, 'base_model__break_ties': False, 'base_model__cache_size': 200, 'base_model__class_weight': 'balanced', 'base_model__coef0': 0.0, 'base_model__decision_function_shape': 'ovr', 'base_model__degree': 3, 'base_model__gamma': 'scale', 'base_model__kernel': 'linear', 'base_model__max_iter': -1, 'base_model__probability': True, 'base_model__random_state': None, 'base_model__shrinking': True, 'base_model__tol': 0.001, 'base_model__verbose': False, 'base_model': SVC(C=11.599674210852156, class_weight='balanced', kernel='linear',
    probability=True), 'threshold': 0.9}


In [21]:
# Define covariates, treatment, and outcome for the CATE model
X_train_cate, X_test_cate, treatment_train, treatment_test, y_train_cate, y_test_cate = define_cate_variables(X_train_scaled, X_test_scaled, y_train, y_test)

# Initialize the SVC model with the correct parameters
#svc_model = SVC(**svc_params)
cate_model = BaseSClassifier(t_svc_model)

# Train the model
cate_model.fit(
        X=X_train_cate,
        treatment=treatment_train,
        y=y_train
    )
# Predict treatment effects on the test set
treatment_effects = cate_model.predict(X_test_cate)

In [22]:
# Get the top customers for treatment
top_customers = get_top_customers_for_treatment(treatment_effects, X_test_scaled, scaler)

# Output business strategy: These are the customers who should receive special treatment to maximize churn reduction.
print("Top 10% customers selected for treatment (unscaled):")
top_customers

Top 10% customers selected for treatment (unscaled):


customer_service_calls  customer_service_rating  customer_happiness  \
835                      6.0                      2.0            0.159844   
443                     25.0                      3.0            0.074842   
603                      0.0                      3.0            0.098843   
615                      0.0                      4.0            0.013837   
1775                    45.0                      3.0            0.103849   
...                      ...                      ...                 ...   
657                      0.0                      5.0            0.256070   
1263                     0.0                      7.0            0.078655   
520                      3.0                      5.0            0.258576   
1530                     7.0                      7.0            0.081112   
628                     15.0                      6.0            0.172974   

      Uplift Score  
835      -0.633142  
443      -0.633032  
603      -0.631745  
615      -0.631382  
1775     -0.631330  
...            ...  
657      -0.504939  
1263     -0.504043  
520      -0.503377  
1530     -0.502509  
628      -0.500986  

[187 rows x 4 columns]

In [23]:
# Estimate the ATE
ate_s, ate_s_lb, ate_s_ub = cate_model.estimate_ate(
    X=X_test_scaled[["customer_service_rating", "customer_happiness"]].values,
    treatment=X_test_scaled["treatment"],
    y=y_test,
    return_ci=True,
    bootstrap_ci=False
    )

# Store results in a dictionary
ate_values = {
    "Upper_limit (ATE)": ate_s_ub,
    "ATE": ate_s,
    "Lower_limit (ATE)": ate_s_lb
}

# Print results
for description, value in ate_values.items():
    print(f"{description}: {value}")

2024-09-07 17:27:06,805 - INFO - Error metrics for group 1
2024-09-07 17:27:06,807 - INFO -      AUC   (Control):     0.8105
2024-09-07 17:27:06,809 - INFO -      AUC (Treatment):     0.8946
2024-09-07 17:27:06,810 - INFO - Log Loss   (Control):     0.4525
2024-09-07 17:27:06,811 - INFO - Log Loss (Treatment):     0.0961


Upper_limit (ATE): [-0.2254092]
ATE: [-0.26233354]
Lower_limit (ATE): [-0.29925788]


In [24]:
# Flatten the treatment_effects array to 1D
treatment_effects_flat = treatment_effects.flatten()

# Create a histogram of the treatment effects
create_histogram(treatment_effects_flat)

In [25]:
# Reset the indices of X_test_scaled and y_test to ensure they match
X_test_scaled = X_test_scaled.reset_index(drop=True)
y_test = y_test.reset_index(drop=True)

# Split and subset based on customer service rating (high/low)
rating_threshold = X_test_scaled['customer_service_rating'].median()
high_rating_group, low_rating_group, y_high_rating, y_low_rating = split_and_subset(X_test_scaled, y_test, 'customer_service_rating', rating_threshold)

# Split and subset based on customer happiness (high/low)
happiness_threshold = X_test_scaled['customer_happiness'].median()
high_happiness_group, low_happiness_group, y_high_happiness, y_low_happiness = split_and_subset(X_test_scaled, y_test, 'customer_happiness', happiness_threshold)

# Split and subset based on treatment group (treatment/control)
treatment_threshold = 0.5  # Assuming binary treatment with 0 and 1
treatment_group, control_group, y_treatment, y_control = split_and_subset(X_test_scaled, y_test, 'treatment', treatment_threshold)

In [26]:
# Customer Service Rating Balance Check
perform_ttest(treatment_group, control_group, 'customer_service_rating')

# Customer Happiness Balance Check
perform_ttest(treatment_group, control_group, 'customer_happiness')

T-test for customer_service_rating: t-statistic = -0.7998820104479232, p-value = 0.42388059472738737
T-test for customer_happiness: t-statistic = 0.040373406386260254, p-value = 0.9677997344944831


In [27]:
cate_estimates = calculate_cate_estimates(kf, X_test_scaled, y_test, thresholded_svc)
print_cate_statistics(cate_estimates)

Mean CATE across folds: 0.08733991212172097
Variance of CATE across folds: 2.7632996239367215e-05


In [28]:
# Calculate the overall ATE (mean of all treatment effects)
ATE = np.mean(treatment_effects)
print(f"ATE: {ATE}")

# Calculate and print CATE for specific subgroups and their differences from ATE
subgroups = {
    "High Rating Group": high_rating_group.index,
    "Low Rating Group": low_rating_group.index,
    "High Happiness Group": high_happiness_group.index,
    "Low Happiness Group": low_happiness_group.index,
    "Treatment_Group": treatment_group.index,
    "Control_Group": control_group.index,
}

for name, indices in subgroups.items():
    CATE = treatment_effects[indices].mean()
    print(f"CATE for {name}: {CATE}")
    print(f"Difference between ATE and CATE ({name}): {CATE - ATE}")

ATE: -0.24982499346076112
CATE for High Rating Group: -0.18812289234104723
Difference between ATE and CATE (High Rating Group): 0.06170210111971389
CATE for Low Rating Group: -0.3090125888922108
Difference between ATE and CATE (Low Rating Group): -0.05918759543144966
CATE for High Happiness Group: -0.13035868032450706
Difference between ATE and CATE (High Happiness Group): 0.11946631313625405
CATE for Low Happiness Group: -0.3691639437898337
Difference between ATE and CATE (Low Happiness Group): -0.11933895032907257
CATE for Treatment_Group: -0.2506762360862209
Difference between ATE and CATE (Treatment_Group): -0.0008512426254597971
CATE for Control_Group: -0.24717606081706067
Difference between ATE and CATE (Control_Group): 0.002648932643700447


In [29]:
# Combine X_test_scaled and y_test into one DataFrame
test_model = X_test_scaled.copy()
test_model['churn'] = y_test  # Add the target variable

# Perform the placebo test
test_model['placebo_treatment'] = np.random.permutation(test_model['treatment'])

# Subset the placebo group and get treatment effects
placebo_group = test_model[test_model['placebo_treatment'] == 1]
X_placebo = placebo_group.drop(columns=['churn', 'placebo_treatment'])
y_placebo = placebo_group['churn']

# Predict treatment effects and calculate CATE for the placebo group
placebo_effects = thresholded_svc.predict_proba(X_placebo)[:, 1]
CATE_placebo = np.mean(placebo_effects)

print(f"CATE for Placebo Group: {CATE_placebo}")


CATE for Placebo Group: 0.08660045407853387


In [30]:
high_rating_results = eval_model_performance(thresholded_svc, high_rating_group, y_high_rating, subgroup_name="High Customer Service Rating Group")
low_rating_results = eval_model_performance(thresholded_svc, low_rating_group, y_low_rating, subgroup_name="Low Customer Service Rating Group")

--- High Customer Service Rating Group ---
Precision: 0.95
Recall: 0.3114754098360656
F1-Score: 0.4691358024691358
PR AUC: 0.7173370563094569
Confusion Matrix:
[[856   1]
 [ 42  19]]
--- Low Customer Service Rating Group ---
Precision: 0.9259259259259259
Recall: 0.24509803921568626
F1-Score: 0.3875968992248062
PR AUC: 0.772856553388588
Confusion Matrix:
[[853   2]
 [ 77  25]]


In [31]:
high_happiness_results = eval_model_performance(thresholded_svc, high_happiness_group, y_high_happiness, subgroup_name="High Customer Happiness Group")
low_happiness_results = eval_model_performance(thresholded_svc, low_happiness_group, y_low_happiness, subgroup_name="Low Customer Happiness Group")

--- High Customer Happiness Group ---
Precision: 0.8333333333333334
Recall: 0.16666666666666666
F1-Score: 0.2777777777777778
PR AUC: 0.6911528547272224
Confusion Matrix:
[[906   1]
 [ 25   5]]
--- Low Customer Happiness Group ---
Precision: 0.9512195121951219
Recall: 0.2932330827067669
F1-Score: 0.4482758620689655
PR AUC: 0.7692889770017041
Confusion Matrix:
[[803   2]
 [ 94  39]]
